# Test note book 

In this test we're using echo algorythm for it's ease of use and to demonstrate the capabilities and functionality of copa backend API. 

Please make sure you have *copa_backend_url* , *client_id* and *url_token* set in /projects/.maap/maap.ini


### Import and configuration
Let's begin with importing the libraries we need and all the configuration we have, you can find them in /projects/.maap/ folder.

In [1]:
import configparser
import os
import requests
import json
import time

In [2]:
#Load the file that contains auth values
config = configparser.ConfigParser()
config.read('/projects/.maap/auth.ini')

#Retrieve auth values
email = config['auth']['email']
password = config['auth']['password']

In [3]:
#Load the file that contains maap values
config = configparser.ConfigParser()
config.read('/projects/.maap/maap.ini')

#Retrieve maap values
copa_backend_url = config['maap']['copa_backend_url']
CLIENT_ID = config['maap']['client_id']
url_token = config['maap']['url_token']
echo_cwl = 'https://s3public.oss.eu-west-0.prod-cloud-ocb.orange-business.com/cwl/echo-test/workflow.cwl'

#Location for tmp file for created process
JobIdWD = '{}/TestJobID.csv'.format(os.path.abspath(os.getcwd()))
print(JobIdWD)

/projects/demo-scripts/wps_notebook/wpst_test/TestJobID.csv


### Authentication
Get an authentication token that will allow us to acces copa API service.

In [4]:
response = requests.post(url_token, data={'client_id': CLIENT_ID, 'username': email, 'password': password, "grant_type": "password", "scope": "profile"})
data = json.loads(response.text)
oauth_token = data['access_token']

### Deployement
Lets start by getting all deployed processes

In [5]:
# get deployed cwl workflow
process = requests.get(copa_backend_url+'wpst/processes', headers = {'Authorization': 'Bearer '+ oauth_token})
print(process.content)

b'{"processes":[]}'


In the next step we will check if echo process is already deployed.

In [6]:
# get echo-wf id if exist
process_already_deployed = None
if process.content:
    for item in json.loads(process.content).get("processes"):
        if item.get('title')== 'wf-echo-process':
            process_already_deployed = item.get('id')
print(process_already_deployed)

None


We cannot have multiple deployement of the same process, and in order to test deploying using the deploy endpoint we have to undeploy the existing one first. 

In [7]:
if process_already_deployed:
    delete_response = requests.delete(copa_backend_url+'wpst/processes/{}'.format(process_already_deployed), headers = {'Authorization': 'Bearer '+ oauth_token})
    print(delete_response.content)

Test deploy endpoint. 

In [8]:
#deploy wf-s1-tiling

wfstorage =  {"executionUnit": [{"href": "{}".format(echo_cwl)}]}
workflow = requests.post(
                        copa_backend_url+'wpst/processes/', 
                        headers = {'Authorization': 'Bearer '+ oauth_token}, 
                        json=wfstorage)
print(workflow.content)
workflow_id = json.loads(workflow.content).get('processSummary').get('id')


b'{"processSummary":{"id":"6455224a9f0e9b5a11d2fd82","title":"wf-echo-test","keywords":null,"owsContext":null,"metadata":null,"additionalParameters":null,"links":null,"version":null,"jobControlOptions":null,"outputTransmission":null,"processDescriptionURL":"https://s3public.oss.eu-west-0.prod-cloud-ocb.orange-business.com/cwl/echo-test/workflow.cwl","abstract":"Applies s expressions to EO acquisitions"}}'


### workflow description

In the next step we will ask the Api endpoint to give us description of the process we just deployed. we can see many informations and most importantly the inputs to launch a job.

In [9]:
wf_description = requests.get(copa_backend_url+'wpst/processes/{}'.format(workflow_id), headers = {'Authorization': 'Bearer '+ oauth_token}) 


In [10]:
print(json.loads(wf_description.content).get('process').get('inputs')[0])

{'id': 'input_reference', 'title': 'Input product reference', 'keywords': ['default: https://earth-search.aws.element84.com/v0/collections/sentinel-s2-l2a-cogs/items/S2B_36RTT_20191205_0_L2A'], 'owsContext': None, 'metadata': None, 'additionalParameters': None, 'links': None, 'minOccurs': None, 'maxOccurs': None, 'formats': [{'mimeType': 'string[]', 'schema': None, 'encoding': None, 'maximumMegabytes': None, 'default': False}], 'abstract': 'Input product reference'}


In [11]:
for item in json.loads(wf_description.content).get('process').get('inputs'):
    print("id : {} \t\t||\t title : {}".format(item.get('id'), item.get('title')))

id : input_reference 		||	 title : Input product reference
id : s_expression 		||	 title : s expression
id : cbn 		||	 title : cbn
id : bucket_name 		||	 title : Stage-in source bucket
id : copy_dir_or_file 		||	 title : Stage-in mode (dir or file)
id : s3_destination 		||	 title : Stage-out target folder


Based on the Description we have above, we can create a payload of input values. this payload will be used to launch a job.

In [12]:
payload = {
  "inputs": [
    {
      "id": "input_file",
      "data": "https://earth-search.aws.element84.com/v0/collections/sentinel-s2-l2a-cogs/items/S2B_36RTT_20191205_0_L2A",
      "href": ""
    },
    {
      "id": "s_message",
      "data": "Hello",
      "href": ""
    },
    {
      "id": "bucket_name",
      "data": "maap-scientific-data",
      "href": ""
    },
    {
      "id": "copy_dir_or_file",
      "data": "file",
      "href": ""
    },
    {
      "id": "s3_destination",
      "data": "maap-scientific-data/shared/demo/echo-process-out",
      "href": ""
    }
  ],
  "outputs": [],
  "mode": "ASYNC",
  "response": "RAW"
}

### Launching a Job

To not cause confusion, we need to define a job in our context. when launching a process, it create an execution instance, and we will call it a job from now on.

The folowing request demonstrate the possibility of launching a process and get the job id.

In [13]:
wf_exec = requests.post(copa_backend_url+'wpst/processes/{}/jobs'.format(workflow_id), json=payload, headers = {'Authorization': 'Bearer '+ oauth_token})
job_id = json.loads(wf_exec.content).get('jobId')
print(wf_exec)

<Response [201]>


In [14]:
# List the executions of the echo workflow 
exec_list = requests.get(copa_backend_url+'wpst/processes/{}/jobs'.format(workflow_id), headers = {'Authorization': 'Bearer '+ oauth_token})
print(exec_list.content)

b'{"jobs":["6455224b9f0e9b5a11d2fd84"]}'


In the previous step we asked the API to provide us with a List of the executions of the CWL workflow with the given ID.

In the next step we check if the job_id we just created is returned in the list.

In [15]:
jobs_list = json.loads(exec_list.content).get("jobs")
assert job_id in jobs_list

#### Job Status

Get job status.

In [16]:
print('please wait...')
job_status=None
while not job_status or json.loads(job_status.content).get('status') == 'RUNNING':
    time.sleep(10)
    job_status = requests.get(copa_backend_url+'wpst/processes/{}/jobs/{}'.format(workflow_id, job_id), headers = {'Authorization': 'Bearer '+ oauth_token})
print(job_status.content)

please wait...
b'{"jobId":"6455224b9f0e9b5a11d2fd84","status":"FAILED","message":"https://argo.dev.esa-maap.org/workflows/argo/exec-wf-echo-test-2023-05-05-15-35-39-wpst","progress":null}'


#### Delete Job

In [17]:
deleted_proc = requests.delete('{}wpst/processes/{}/jobs/{}'.format(copa_backend_url, workflow_id, job_id), 
                               headers = {'Authorization': 'Bearer '+ oauth_token})
print(deleted_proc.content)

b'{"id":"6455224b9f0e9b5a11d2fd84"}'


#### Undeploy process.

In [18]:
requests.delete(copa_backend_url+'wpst/processes/{}'.format(workflow_id), headers = {'Authorization': 'Bearer '+ oauth_token})

<Response [200]>